In [1]:
%reload_ext autoreload
%autoreload 2


In [2]:
import os
import yaml
import urllib
from PIL import Image
from enum import Enum
from pycocotools.coco import COCO
import xml.etree.cElementTree as ET
import glob
import argparse
import numpy as np
import json
import numpy
import cv2
from collections import OrderedDict
import scipy.misc
from skimage import measure   
import random
import skimage.io as io
import matplotlib.pyplot as plt
import pylab
import shutil
import pickle
import pandas as pd
from subprocess import Popen,PIPE,STDOUT,call 
from utils import datasets

BDD100K_DIRECTORY = os.path.join('/media/dean/datastore/datasets/BerkeleyDeepDrive', 'bdd100k')
WORKING_DIRECTORY = '/media/dean/datastore/datasets/darknet'

TRAINERS_DIRECTORY = os.path.join(WORKING_DIRECTORY, 'trainers')
ANNOTATIONS_FILE = os.path.join(BDD100K_DIRECTORY, 'labels/bdd100k_labels_images_train.json')

VAL_ANNOTATIONS_FILE = os.path.join(BDD100K_DIRECTORY, 'labels/bdd100k_labels_images_val.json')
COCO_ANNOTATIONS_FILE = os.path.join('/media/dean/datastore/datasets/road_coco/darknet/data/coco/annotations/instances_train2014.json')

BASE_DATA_CONFIG = os.path.join(WORKING_DIRECTORY, 'cfg', 'bdd100k.data')
BASE_MODEL_CONFIG = os.path.join(WORKING_DIRECTORY, 'cfg', 'yolov3-bdd100k.cfg')

In [3]:
# Prepare Dataset ##



bddcoco_set = datasets.DataFormatter(annotations_list = ANNOTATIONS_FILE, input_format = datasets.Format.bdd, use_cache = True,
                                 output_path = os.path.join(WORKING_DIRECTORY,'data/bddcoco_set'),
                                 trainer_prefix = 'COCO_train2014_0000', 
                                 s3_bucket = 'kache-scalabel/bdd100k/images/100k/train/')



Saving to Pickle File: BerkeleyDeepDrive_bdd100k_labels_bdd100k_labels_images_train.json.pickle
Length of COCO Images 69863
Length of COCO Annotations: 1286871
loading annotations into memory...
Done (t=7.26s)
creating index...
index created!

########### DATASET DISTRIBUTION: ###########

BIKE | Annotations: 7210  | Images:  4343
BUS | Annotations: 11672  | Images:  8993
CAR | Annotations: 713211  | Images:  69072
MOTOR | Annotations: 3002  | Images:  2284
PERSON | Annotations: 91349  | Images:  22076
RIDER | Annotations: 4517  | Images:  3586
TRAFFIC LIGHT | Annotations: 57176  | Images:  20386
TRAFFIC LIGHT-AMBER | Annotations: 3417  | Images:  2048
TRAFFIC LIGHT-GREEN | Annotations: 79406  | Images:  29193
TRAFFIC LIGHT-RED | Annotations: 46118  | Images:  18644
TRAFFIC SIGN | Annotations: 239686  | Images:  57154
TRAIN | Annotations: 136  | Images:  105
TRUCK | Annotations: 29971  | Images:  18890

################################################



In [4]:
coco_set = datasets.DataFormatter(annotations_list = COCO_ANNOTATIONS_FILE, input_format = datasets.Format.coco,
                                 output_path = os.path.join(WORKING_DIRECTORY,'data/coco_set'),use_cache = False,
                                 trainer_prefix = 'COCO_train2014_0000', 
                                 s3_bucket = 'kache-scalabel/coco_dataset/images/train2014/')


In [5]:
coco_set = datasets.DataFormatter(annotations_list = '/media/dean/datastore/datasets/darknet/data/coco_set/bdd100k/annotations/bdd100k_altered_annotations2.json', input_format = datasets.Format.bdd,
                                 output_path = os.path.join(WORKING_DIRECTORY,'data/coco_set'),use_cache = True,
                                 trainer_prefix = 'COCO_train2014_0000', 
                                 s3_bucket = 'kache-scalabel/coco_dataset/images/train2014/')


Length of COCO Images 82081
Length of COCO Annotations: 604907
loading annotations into memory...
Done (t=4.56s)
creating index...
index created!

########### DATASET DISTRIBUTION: ###########

AIRPLANE | Annotations: 3833  | Images:  2243
APPLE | Annotations: 4308  | Images:  1171
BACKPACK | Annotations: 6200  | Images:  3924
BANANA | Annotations: 6912  | Images:  1618
BASEBALL BAT | Annotations: 2400  | Images:  1804
BASEBALL GLOVE | Annotations: 2689  | Images:  1884
BEAR | Annotations: 903  | Images:  668
BED | Annotations: 2905  | Images:  2539
BENCH | Annotations: 6751  | Images:  3844
BICYCLE | Annotations: 4955  | Images:  2287
BIRD | Annotations: 7290  | Images:  2241
BOAT | Annotations: 7590  | Images:  2098
BOOK | Annotations: 17315  | Images:  3734
BOTTLE | Annotations: 16983  | Images:  5968
BOWL | Annotations: 10064  | Images:  5028
BROCCOLI | Annotations: 4927  | Images:  1340
BUS | Annotations: 4327  | Images:  2791
CAKE | Annotations: 4551  | Images:  2080
CAR | Annota

In [6]:
bddcoco_set.merge(coco_set, include=['CONSTRUCT-BARREL','dog', 'cell phone', 'CONSTRUCT-CONE','CONSTRUCT-EQUIPMENT', 'CONSTRUCT-POLE', 'CONSTRUCT-POST', 'CONSTRUCT-SIGN', 'person', 'train', 'truck', 'car', 'traffic light', 'traffic light-red','traffic light-amber','traffic light-green', 'bus', 'bike', 'motor', 'traffic sign','traffic sign-slow_sign', 'rider','traffic sign-speed_sign', 'traffic sign-stop_sign'], reject_new_categories = True)

APPENDING to delete list: COCO_train2014_000000077020.jpg
APPENDING to delete list: COCO_train2014_000000044953.jpg
APPENDING to delete list: COCO_train2014_000000393844.jpg
APPENDING to delete list: COCO_train2014_000000277885.jpg
APPENDING to delete list: COCO_train2014_000000134946.jpg
APPENDING to delete list: COCO_train2014_000000383805.jpg
APPENDING to delete list: COCO_train2014_000000539173.jpg
APPENDING to delete list: COCO_train2014_000000302354.jpg
APPENDING to delete list: COCO_train2014_000000338323.jpg
APPENDING to delete list: COCO_train2014_000000391492.jpg
APPENDING to delete list: COCO_train2014_000000406725.jpg
APPENDING to delete list: COCO_train2014_000000545611.jpg
APPENDING to delete list: COCO_train2014_000000269749.jpg
APPENDING to delete list: COCO_train2014_000000321324.jpg
APPENDING to delete list: COCO_train2014_000000293980.jpg
APPENDING to delete list: COCO_train2014_000000421991.jpg
APPENDING to delete list: COCO_train2014_000000573572.jpg
APPENDING to d

APPENDING to delete list: COCO_train2014_000000101155.jpg
APPENDING to delete list: COCO_train2014_000000343012.jpg
APPENDING to delete list: COCO_train2014_000000270079.jpg
APPENDING to delete list: COCO_train2014_000000488043.jpg
APPENDING to delete list: COCO_train2014_000000508701.jpg
APPENDING to delete list: COCO_train2014_000000436626.jpg
APPENDING to delete list: COCO_train2014_000000172276.jpg
APPENDING to delete list: COCO_train2014_000000484347.jpg
APPENDING to delete list: COCO_train2014_000000226795.jpg
APPENDING to delete list: COCO_train2014_000000481648.jpg
APPENDING to delete list: COCO_train2014_000000203969.jpg
APPENDING to delete list: COCO_train2014_000000225230.jpg
APPENDING to delete list: COCO_train2014_000000032093.jpg
APPENDING to delete list: COCO_train2014_000000355628.jpg
APPENDING to delete list: COCO_train2014_000000240376.jpg
APPENDING to delete list: COCO_train2014_000000026108.jpg
APPENDING to delete list: COCO_train2014_000000292688.jpg
APPENDING to d

APPENDING to delete list: COCO_train2014_000000546065.jpg
APPENDING to delete list: COCO_train2014_000000285307.jpg
APPENDING to delete list: COCO_train2014_000000059321.jpg
APPENDING to delete list: COCO_train2014_000000478505.jpg
APPENDING to delete list: COCO_train2014_000000342184.jpg
APPENDING to delete list: COCO_train2014_000000340699.jpg
APPENDING to delete list: COCO_train2014_000000297639.jpg
APPENDING to delete list: COCO_train2014_000000352814.jpg
APPENDING to delete list: COCO_train2014_000000001168.jpg
APPENDING to delete list: COCO_train2014_000000375455.jpg
APPENDING to delete list: COCO_train2014_000000537720.jpg
APPENDING to delete list: COCO_train2014_000000297091.jpg
APPENDING to delete list: COCO_train2014_000000199427.jpg
APPENDING to delete list: COCO_train2014_000000321702.jpg
APPENDING to delete list: COCO_train2014_000000488564.jpg
APPENDING to delete list: COCO_train2014_000000423964.jpg
APPENDING to delete list: COCO_train2014_000000143339.jpg
APPENDING to d

APPENDING to delete list: COCO_train2014_000000191156.jpg
APPENDING to delete list: COCO_train2014_000000519894.jpg
APPENDING to delete list: COCO_train2014_000000249429.jpg
APPENDING to delete list: COCO_train2014_000000232987.jpg
APPENDING to delete list: COCO_train2014_000000008731.jpg
APPENDING to delete list: COCO_train2014_000000119534.jpg
APPENDING to delete list: COCO_train2014_000000045153.jpg
APPENDING to delete list: COCO_train2014_000000478375.jpg
APPENDING to delete list: COCO_train2014_000000231387.jpg
APPENDING to delete list: COCO_train2014_000000223660.jpg
APPENDING to delete list: COCO_train2014_000000203107.jpg
APPENDING to delete list: COCO_train2014_000000403837.jpg
APPENDING to delete list: COCO_train2014_000000484201.jpg
APPENDING to delete list: COCO_train2014_000000556417.jpg
APPENDING to delete list: COCO_train2014_000000551836.jpg
APPENDING to delete list: COCO_train2014_000000091797.jpg
APPENDING to delete list: COCO_train2014_000000455879.jpg
APPENDING to d

APPENDING to delete list: COCO_train2014_000000038487.jpg
APPENDING to delete list: COCO_train2014_000000381947.jpg
APPENDING to delete list: COCO_train2014_000000213897.jpg
APPENDING to delete list: COCO_train2014_000000063147.jpg
APPENDING to delete list: COCO_train2014_000000021535.jpg
APPENDING to delete list: COCO_train2014_000000182098.jpg
APPENDING to delete list: COCO_train2014_000000163639.jpg
APPENDING to delete list: COCO_train2014_000000208011.jpg
APPENDING to delete list: COCO_train2014_000000465220.jpg
APPENDING to delete list: COCO_train2014_000000446945.jpg
APPENDING to delete list: COCO_train2014_000000196156.jpg
APPENDING to delete list: COCO_train2014_000000528119.jpg
APPENDING to delete list: COCO_train2014_000000155102.jpg
APPENDING to delete list: COCO_train2014_000000002284.jpg
APPENDING to delete list: COCO_train2014_000000413776.jpg
APPENDING to delete list: COCO_train2014_000000050636.jpg
APPENDING to delete list: COCO_train2014_000000067114.jpg
APPENDING to d

...

PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778

PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778

PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778

PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778

PRUNING the ANNOTATION deletions (207403 total)
Successfully merged 53303 images | and  260378 annotations
Length of COCO Annotations: 1547249
loading annotations into memory...
Done (t=8.02s)
creating index...
index created!

########### DATASET DISTRIBUTION: ###########

BICYCLE | Annotations: 4955  | Images:  2287
BIKE | Annotations: 7210  | Images:  4343
BUS | Annotations: 15999  | Images:  11784
CAR | Annotations: 743996  | Images:  77678
CELL PHONE | Annotations: 4460  | Images:  3322
DOG | Annotations: 3774  | Images:  3041
MOTOR | Annotations: 3002  | Images:  2284
MOTORCYCLE | Annotations: 6021  | Images:  2442
PERSON | Annotations: 276665  | Images:  67250
RIDER | Annotations: 4517  | Images:  3586
STOP SIGN | Annotations: 1372  | Images:  1214
TRAFFIC LIGHT | Annotations: 66335  | Images:  23279
TRAFFIC LIGHT-AMBER | Annotations: 3417  | Images:  2048
TRAFFIC LIGHT-GREEN | Annotations: 79406  | Images:  29193
TRAFFIC LIGHT-RED | Annotations: 46118  | Images:  18644
TRAFFIC S

In [7]:
bddcoco_set.export(format = datasets.Format.bdd, paginate = False)

In [ ]:
annotations_file = '/media/dean/datastore/datasets/darknet/data/bddcoco_set/bdd100k/annotations/bdd100k_altered_annotations.json'
!cd $WORKING_DIRECTORY && python3 darkernet.py -b 'kache-scalabel/kache_ai/frames/' -a $annotations_file -f BDD -r True

Saving to Pickle File: darknet_data_bddcoco_set_bdd100k_annotations_bdd100k_altered_annotations.json.pickle
Length of COCO Images 123166
Length of COCO Annotations: 1547249
loading annotations into memory...
Done (t=10.96s)
creating index...
index created!

########### DATASET DISTRIBUTION: ###########

BIKE | Annotations: 12165  | Images:  6630
BUS | Annotations: 15999  | Images:  11784
CAR | Annotations: 743996  | Images:  77678
CELL PHONE | Annotations: 4460  | Images:  3322
DOG | Annotations: 3774  | Images:  3041
MOTOR | Annotations: 9023  | Images:  4726
PERSON | Annotations: 276665  | Images:  67250
RIDER | Annotations: 4517  | Images:  3586
TRAFFIC LIGHT | Annotations: 66335  | Images:  23279
TRAFFIC LIGHT-AMBER | Annotations: 3417  | Images:  2048
TRAFFIC LIGHT-GREEN | Annotations: 79406  | Images:  29193
TRAFFIC LIGHT-RED | Annotations: 46118  | Images:  18644
TRAFFIC SIGN | Annotations: 241058  | Images:  58368
TRAIN | Annotations: 3295  | Images:  2569
TRUCK | Annotations: 

COCO Parsing:  |███-------------------------------------| 7.8% (120409/1547249)  Complete

COCO Parsing:  |█████-----------------------------------| 12.8% (198223/1547249)  Complete-----------------| 7.8% (120577/1547249)  Complete----| 7.8% (121110/1547249)  Complete249)  Complete----| 7.9% (122385/1547249)  Complete----| 8.0% (123150/1547249)  Complete----| 8.0% (123235/1547249)  Complete�█-------------------------------------| 8.0% (123426/1547249)  Complete�█-------------------------------------| 8.0% (123596/1547249)  Complete�█-------------------------------------| 8.0% (124531/1547249)  Complete�█-------------------------------------| 8.1% (125466/1547249)  Complete�█-------------------------------------| 8.1% (125976/1547249)  Complete�█-------------------------------------| 8.2% (126231/1547249)  Complete----| 8.2% (126380/1547249)  Complete----| 8.3% (127740/1547249)  Complete�█-------------------------------------| 8.3% (128441/1547249)  Complete----| 8.3% (128675/1547249)  Complete249)  Complete----| 8.4% (129950/1547249)  Complete�█------------------------------

COCO Parsing:  |█████-----------------------------------| 14.1% (218635/1547249)  Complete��███-----------------------------------| 12.8% (198425/1547249)  Complete��███-----------------------------------| 12.8% (198749/1547249)  Complete��███-----------------------------------| 12.9% (198911/1547249)  Complete��███-----------------------------------| 12.9% (198992/1547249)  Complete��███-----------------------------------| 12.9% (199073/1547249)  Complete1547249)  Complete��███-----------------------------------| 12.9% (199721/1547249)  Complete1547249)  Complete��███-----------------------------------| 12.9% (200045/1547249)  Complete��███-----------------------------------| 13.0% (200369/1547249)  Complete------| 13.0% (200430/1547249)  Complete��███-----------------------------------| 13.0% (200693/1547249)  Complete��███-----------------------------------| 13.0% (200774/1547249)  Complete��███-----------------------------------| 13.0% (200855/1547249)  Complete------| 13.0% (20107

COCO Parsing:  |██████----------------------------------| 15.3% (236505/1547249)  Complete1547249)  Complete1547249)  Complete��███-----------------------------------| 14.2% (219161/1547249)  Complete------| 14.2% (219384/1547249)  Complete��███-----------------------------------| 14.2% (219566/1547249)  Complete1547249)  Complete1547249)  Complete------| 14.2% (219951/1547249)  Complete1547249)  Complete1547249)  Complete1547249)  Complete1547249)  Complete1547249)  Complete1547249)  Complete------| 14.3% (220923/1547249)  Complete��███-----------------------------------| 14.3% (221024/1547249)  Complete------| 14.3% (221166/1547249)  Complete��███-----------------------------------| 14.3% (221267/1547249)  Complete��███-----------------------------------| 14.3% (221429/1547249)  Complete��███-----------------------------------| 14.3% (221672/1547249)  Complete��███-----------------------------------| 14.3% (221753/1547249)  Complete------| 14.3% (221814/1547249)  Complete��███-------

...

YOLO Saving:   |�████████████████████-------------------| 54.9% (5495/10000)  Complete2861/10000)  Completee��██████████-----------------------------| 29.0% (2898/10000)  Complete████-----------------------------| 29.2% (2916/10000)  Complete---------------------| 29.3% (2934/10000)  Complete-| 29.5% (2952/10000)  Complete)  Complete-----------------------| 29.7% (2973/10000)  Complete---| 29.9% (2991/10000)  Complete---| 30.1% (3009/10000)  Complete-------------------| 30.3% (3027/10000)  Complete�██----------------------------| 30.4% (3045/10000)  Complete��███████----------------------------| 30.6% (3063/10000)  Complete  |████████████----------------------------| 30.8% (3081/10000)  Complete---| 30.8% (3083/10000)  Complete-------------------| 31.0% (3101/10000)  Complete�██----------------------------| 31.2% (3119/10000)  Complete��███████----------------------------| 31.4% (3137/10000)  Complete  |████████████----------------------------| 31.6% (3155/10000)  Completee/10000)  Com

YOLO Saving:   |██████████████████████████████----------| 76.4% (7638/10000)  Completee�████------------------| 55.1% (5513/10000)  Complete-----------| 55.3% (5528/10000)  Complete5543/10000)  Completee��█████████████████████------------------| 55.7% (5574/10000)  Complete███████████████------------------| 55.9% (5589/10000)  Complete�████████------------------| 56.0% (5604/10000)  Complete�------------------| 56.1% (5606/10000)  Complete 56.2% (5621/10000)  Complete Completeng:   |██████████████████████------------------| 56.5% (5652/10000)  Complete��█████████████████------------------| 56.7% (5667/10000)  Complete███████████------------------| 56.8% (5682/10000)  Complete�████------------------| 57.0% (5697/10000)  Complete-------| 57.0% (5699/10000)  Complete/10000)  CompleteOLO Saving:   |██████████████████████------------------| 57.3% (5730/10000)  Complete�████████████████████------------------| 57.5% (5745/10000)  Complete�█████████████████████-----------------| 57.6% (5760/10

YOLO Saving:   |██████████████████████████████████████--| 96.3% (9632/10000)  Completete/10000)  Complete�████████████████----------| 76.8% (7680/10000)  Complete00)  Complete███████████████----------| 77.1% (7707/10000)  Complete��█████████████████----------| 77.1% (7709/10000)  Complete/10000)  Complete�████████████████----------| 77.4% (7736/10000)  Complete00)  Complete��████████████████████████---------| 77.6% (7763/10000)  Complete████████---------| 77.8% (7776/10000)  Complete00)  Complete9% (7791/10000)  Complete��████████████████████████████---------| 78.0% (7805/10000)  Complete████████████---------| 78.2% (7818/10000)  Complete3% (7831/10000)  Complete��████████████████████████████---------| 78.5% (7845/10000)  Complete████████████---------| 78.6% (7858/10000)  Complete7% (7871/10000)  Complete-------| 78.7% (7873/10000)  Complete:   |███████████████████████████████---------| 78.9% (7887/10000)  Complete████████████████---------| 79.0% (7900/10000)  Complete-------| 79.1% (7

YOLO Saving:   |████████████████████████████████████████| 100.0% (10000/10000)  Complete0)  Complete��█████████████████████████████████████--| 96.7% (9670/10000)  Complete9671/10000)  Completeng:   |██████████████████████████████████████--| 96.8% (9684/10000)  Complete��█████████████████████████████--| 97.0% (9696/10000)  Complete███████████████████--| 97.1% (9708/10000)  Complete�████████--| 97.2% (9720/10000)  Complete3% (9732/10000)  CompleteSaving:   |██████████████████████████████████████--| 97.5% (9745/10000)  Complete�--| 97.5% (9746/10000)  Complete58/10000)  Complete)  CompleteeteO Saving:   |███████████████████████████████████████-| 98.0% (9795/10000)  Complete:   |███████████████████████████████████████-| 98.1% (9807/10000)  Complete██████████████████████████████████████-| 98.2% (9819/10000)  Complete (9820/10000)  Complete0000)  Completeompleteving:   |███████████████████████████████████████-| 98.7% (9869/10000)  Complete|███████████████████████████████████████-| 98.8% (988

  35 conv    256  3 x 3 / 1    52 x  52 x 128   ->    52 x  52 x 256 1.595 BF
  36 Shortcut Layer: 33
  37 conv    512  3 x 3 / 2    52 x  52 x 256   ->    26 x  26 x 512 1.595 BF
  38 conv    256  1 x 1 / 1    26 x  26 x 512   ->    26 x  26 x 256 0.177 BF
  39 conv    512  3 x 3 / 1    26 x  26 x 256   ->    26 x  26 x 512 1.595 BF
  40 Shortcut Layer: 37
  41 conv    256  1 x 1 / 1    26 x  26 x 512   ->    26 x  26 x 256 0.177 BF
  42 conv    512  3 x 3 / 1    26 x  26 x 256   ->    26 x  26 x 512 1.595 BF
  43 Shortcut Layer: 40
  44 conv    256  1 x 1 / 1    26 x  26 x 512   ->    26 x  26 x 256 0.177 BF
  45 conv    512  3 x 3 / 1    26 x  26 x 256   ->    26 x  26 x 512 1.595 BF
  46 Shortcut Layer: 43
  47 conv    256  1 x 1 / 1    26 x  26 x 512   ->    26 x  26 x 256 0.177 BF
  48 conv    512  3 x 3 / 1    26 x  26 x 256   ->    26 x  26 x 512 1.595 BF
  49 Shortcut Layer: 46
  50 conv    256  1 x 1 / 1    26 x  26 x 512   ->    26 x  26 x 256 0.177 BF
  51 conv    512  3 x 

In [9]:
# KACHE_S3 = 'kache-scalabel/kache_ai/frames/'
# annotations_file = os.path.join(WORKING_DIRECTORY,'data/kache_set/annotations/Kache-Logs--Tanveer-WithTrafficSigns_partial_complete_1.json')
# !cd $WORKING_DIRECTORY && python3 darkernet.py -a $annotations_file -f BDD -b $KACHE_S3 -r True

In [10]:
# WORKING_DIR = '/media/dean/datastore1/datasets/kache_ai/frames/kache_set/'
# kache_set = datasets.DataFormatter(annotations_list = '/media/dean/datastore1/datasets/kache_ai/frames/kache_set/kacheai_logs.pickle', image_list = '/media/dean/datastore1/datasets/kache_ai/frames/kache_set/', input_format = datasets.Format.kache,
#                                  output_path = os.path.join(WORKING_DIR,'scalabel_files'), use_cache = True,
#                                  trainer_prefix = 'COCO_train2014_0000', pickle_file = '/media/dean/datastore1/datasets/Scripts/kache_ai_frames_kache_set_kacheai_logs.pickle.pickle',
#                                  s3_bucket = 'kache-scalabel/kache_ai/frames/', check_s3 = False, use_static_categories = True)


In [11]:
# kache_set.export(format = datasets.Format.scalabel, paginate = True)

In [12]:
# cocodd_set.merge(coco_set, include=['person', 'train', 'truck', 'car', 'traffic light', 'bus'], reject_new_categories = True)

In [13]:
# cocodd_set.export(format = datasets.Format.bdd, paginate = False)